In [2]:
%load_ext autoreload

In [3]:
%autoreload
import os
import importlib
import itertools
import numpy as np
import pickle
import time

import torch
import torch.nn as nn
from torch.autograd import Variable
import torchvision.datasets as dset
from torchvision.utils import save_image
import torchvision.transforms as transforms

import MNISTM_dataset
from usps_dataset import USPS
from blocks import ResidualBlock, weights_initialization

In [4]:
use_cuda = torch.cuda.is_available()
root = 'data/'
batch_size = 32

latent_dimension = 10
img_channels = 3
img_size = 32
learning_rate = 2e-4
beta_1 = 0.5 
beta_2 = 0.999

## Define the datasets (MNIST, MNIST_M, SVHN):

In [5]:
os.makedirs('data/', exist_ok=True)

In [6]:
trans = transforms.Compose([transforms.Resize(img_size), transforms.ToTensor(), transforms.Normalize((0.5, 0.5, 0.5),
                                                                                        (0.5, 0.5, 0.5))])

usps_trans = transforms.Compose([transforms.Resize(img_size),
                                 transforms.ToTensor(), 
                                 transforms.Normalize((0.5, 0.5, 0.5),(0.5, 0.5, 0.5))])

In [7]:
mnist = torch.load("data/processed/training.pt")

In [8]:
mnist2 = (mnist[0][0:25],mnist[1][0:100])

In [9]:
mnist_m = torch.load("data/processed/mnist_m_train.pt")

In [10]:
mnist_m_2 = (mnist_m[0][0:25],mnist[1][0:25])

In [12]:
# torch.save(mnist_m_2, "data_small/processed/mnist_m_train.pt")

In [13]:
training_set_small = dset.MNIST(root="data_small/", train=True, transform=trans, download=False)

In [14]:
training_set_small_m = MNISTM_dataset.MNISTM(root="data_small/", train=True, transform=trans, download=False)

In [15]:
training_set_original = dset.MNIST(root=root, train=True, transform=trans, download=False)
test_set_original = dset.MNIST(root=root, train=False, transform=trans, download=False)

In [16]:
training_set_m = MNISTM_dataset.MNISTM(root=root, train=True, transform=trans, download=False)
test_set_m = MNISTM_dataset.MNISTM(root=root, train=False, transform=trans, download=False)

In [19]:
training_usps = USPS(root=root, train=True,transform=usps_trans, download=False)
test_usps = USPS(root=root, train=False,transform=usps_trans, download=False)

In [20]:
dataloader_small = torch.utils.data.DataLoader(training_set_small, batch_size=10, 
                                                  shuffle=False, num_workers=6, pin_memory=True, drop_last=True)

In [21]:
dataloader_small_m = torch.utils.data.DataLoader(training_set_small_m, batch_size=10, 
                                                  shuffle=False, num_workers=6, pin_memory=True, drop_last=True)

In [22]:
dataloader_base = torch.utils.data.DataLoader(training_set_original, batch_size=10, 
                                                  shuffle=False, num_workers=6, pin_memory=True, drop_last=True)

dataloader_original = torch.utils.data.DataLoader(training_set_original, batch_size=batch_size, 
                                                  shuffle=True, num_workers=6, pin_memory=True, drop_last=True)
dataloader_MNISTM = torch.utils.data.DataLoader(training_set_m, batch_size=batch_size, 
                                                shuffle=True, num_workers=6, pin_memory=True)

usps_data_loader = torch.utils.data.DataLoader(
        dataset=training_usps,
        batch_size=batch_size, shuffle=True, num_workers=6, pin_memory=True, drop_last=True)

usps_data_loader_L2 = torch.utils.data.DataLoader(
        dataset=training_usps,
        batch_size=1, shuffle=False, num_workers=6, pin_memory=True, drop_last=True)

dataloader_MNISTM_L2 = torch.utils.data.DataLoader(training_set_m, batch_size=1, 
                                                shuffle=False, num_workers=6, pin_memory=True)

dataloader_usps_test = torch.utils.data.DataLoader(test_usps, batch_size=batch_size, 
                                                  shuffle=False, num_workers=6, pin_memory=True)

dataloader_original_test = torch.utils.data.DataLoader(test_set_original, batch_size=batch_size, 
                                                  shuffle=False, num_workers=6, pin_memory=True)
dataloader_MNISTM_test = torch.utils.data.DataLoader(test_set_m, batch_size=batch_size, 
                                                shuffle=False, num_workers=6, pin_memory=True)

## Define PixelDA generator, discriminator and classifier architectures

In [23]:
class Generator(nn.Module):
    def __init__(self, latent_dimension=10, img_channels=img_channels, img_size=32):
        super().__init__()
        
        self.fc = nn.Linear(latent_dimension, 1*img_size**2)
        self.l1 = nn.Sequential(nn.Conv2d(1*2, 64, 3, 1, 1), nn.ReLU(inplace=True))
        
        residual_blocks = []
        
        for i in range(6):
            residual_blocks.append(ResidualBlock())
        self.residual_blocks = nn.Sequential(*residual_blocks)
        
        self.l2 = nn.Sequential(nn.Conv2d(64, img_channels, 3, 1, 1), nn.Tanh())
         
    def forward(self, img, z):
        transformed_noise = self.fc(z).view(*img.shape)
        transformed_input = torch.cat((img, transformed_noise ), 1)
        out = self.l1(transformed_input)
        out = self.residual_blocks(out)
        img = self.l2(out)
        
        return img

In [24]:
class Discriminator(nn.Module):
    def __init__(self):
        super().__init__()
        
        def block(in_features, out_features, normalize=True):
            layers = [nn.Conv2d(in_features, out_features, 3, stride=2, padding=1),
                     nn.LeakyReLU(0.2, inplace=True)]
            if normalize:
                layers.append(nn.InstanceNorm2d(out_features))
            return layers
        
        self.model = nn.Sequential(
            *block(img_channels, 64, normalize=False),
            torch.nn.Dropout(p=0.1),
            *block(64, 128),
            torch.nn.Dropout(p=0.1),
            *block(128,256),
            torch.nn.Dropout(p=0.1),
            *block(256,512),
            torch.nn.Dropout(p=0.1),
            nn.Conv2d(512,1,3,1,1)
        )
        
    def forward(self, img):
        out = self.model(img)
        
        return out

In [25]:
class Classifier_DA(nn.Module):
    def __init__(self, source_channels=1, target_channels=img_channels, num_classes=10):
        super().__init__()

        self.private_source = nn.Sequential(
            nn.Conv2d(source_channels, 32, kernel_size=5, stride=1, padding=2, bias=True),
            nn.ReLU(True),
        )
        
        self.private_target = nn.Sequential(
            nn.Conv2d(target_channels, 32, kernel_size=5, stride=1, padding=2),
            nn.ReLU(True),
        )
            
        self.shared_convs = nn.Sequential(
            nn.Conv2d(32, 48, kernel_size=5, stride=1, padding=2),
            nn.ReLU(True),
            nn.MaxPool2d(kernel_size=2, stride=2, padding=0),
        )
        
        self.shared_fcs = nn.Sequential(
            nn.Linear(12288, 100),
            nn.ReLU(True),
            nn.Linear(100, 100),
            nn.ReLU(True),
            nn.Linear(100, num_classes)
        )

    def forward(self, inputs, dest):
        if dest=="source":
            private_net = self.private_source
        elif dest=="target":
            private_net = self.private_target
        output = private_net(inputs)
        output = self.shared_convs(output)
        output = output.view(output.size(0), -1)
        output = self.shared_fcs(output)
        return output

In [99]:
generator_da, discriminator_da, classifier = Generator(), Discriminator(), Classifier_DA()

if use_cuda: generator_da.cuda(); discriminator_da.cuda(); classifier.cuda()

generator_da.apply(weights_initialization); discriminator_da.apply(weights_initialization); classifier.apply(weights_initialization); 

## Define LSGAN generator and discriminator architectures

In [26]:
class Generator_LS(nn.Module):
    
    def __init__(self, img_size = 32, latent_dim=10, channels=1):
        super().__init__()

        self.init_size = img_size // 4 # why scaled down?
        self.l1 = nn.Sequential(nn.Linear(latent_dim, 128*self.init_size**2))

        self.conv_blocks = nn.Sequential(
            nn.Upsample(scale_factor=2), # this upsampling cannot happen if we use full resolutions...
            nn.Conv2d(128+channels, 128, 3, stride=1, padding=1), # img channel number here
            nn.BatchNorm2d(128, 0.8),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Upsample(scale_factor=2),
            nn.Conv2d(128, 64, 3, stride=1, padding=1),
            nn.BatchNorm2d(64, 0.8),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(64, channels, 3, stride=1, padding=1),
            nn.Tanh()
        )
        self.downsample = nn.Conv2d(channels, channels, 3, stride=2, padding=1)

    def forward(self, img, z):
        out = self.l1(z)
        transformed_noise = out.view(out.shape[0], 128, self.init_size, self.init_size)
        
        #out.view(img.shape[0],128,img.shape[-2],img.shape[-1]) # 128,32,32 should be that - maybe downscale it?

        img_downsampled = self.downsample(self.downsample(img))
#         print(img_downsampled.shape)
#         print(transformed_noise.shape)
        transformed_input = torch.cat((img_downsampled, transformed_noise ), 1)

        
        #         out = self.l1(transformed_input)

#         out = out.view(out.shape[0], 128, self.init_size, self.init_size)
        img = self.conv_blocks(transformed_input)
        return img
    

In [27]:
class Discriminator_LS(nn.Module):
    def __init__(self, channels=img_channels, img_size=32):
        super().__init__()

        def discriminator_block(in_filters, out_filters, bn=True):
            block = [   nn.Conv2d(in_filters, out_filters, 3, 2, 1),
                        nn.LeakyReLU(0.2, inplace=True),
                        nn.Dropout2d(0.25)]
            if bn:
                block.append(nn.BatchNorm2d(out_filters, 0.8))
            return block

        self.model = nn.Sequential(
            *discriminator_block(channels, 16, bn=False),
            *discriminator_block(16, 32),
            *discriminator_block(32, 64),
            *discriminator_block(64, 128),
        )

        # The height and width of downsampled image
        ds_size = img_size // 2**4
        self.adv_layer = nn.Linear(128*ds_size**2, 1)

    def forward(self, img):
        out = self.model(img)
        out = out.view(out.shape[0], -1)
        validity = self.adv_layer(out)

        return validity

In [102]:
generator_ls, discriminator_ls = Generator_LS(), Discriminator_LS()

if use_cuda: generator_ls.cuda(); discriminator_ls.cuda()

generator_ls.apply(weights_initialization); discriminator_ls.apply(weights_initialization);

## Define loss function and optimizers

In [34]:
MSE_loss = torch.nn.MSELoss()
task_loss = torch.nn.CrossEntropyLoss()

if use_cuda: MSE_loss.cuda(); task_loss.cuda()

# Loss hyperparameters:
lambda_gan = 0.05  # 0.05 #0.05
lambda_task = 1 #0.01 # Loss weights

In [104]:
opt_G_DA = torch.optim.Adam(itertools.chain(generator_da.parameters(), classifier.parameters()),
                        lr = learning_rate, betas = (beta_1, beta_2))

opt_D_DA = torch.optim.Adam(itertools.chain(discriminator_da.parameters()),
                        lr = learning_rate, betas = (beta_1, beta_2))

In [105]:
opt_G_LS = torch.optim.Adam(itertools.chain(generator_ls.parameters(), classifier.parameters()), 
                            lr=learning_rate, betas=(beta_1, beta_2))
opt_D_LS = torch.optim.Adam(discriminator_ls.parameters(), lr= learning_rate, betas=(beta_1, beta_2))

In [31]:
FloatTensor = torch.cuda.FloatTensor if use_cuda else torch.FloatTensor
LongTensor = torch.cuda.LongTensor if use_cuda else torch.LongTensor

## GAN Training (unsupervised target domain)

In [107]:
patch = int(img_size / 2**4)
patch =  (1,) #(1, patch, patch) # - network dependent # (1,)

In [108]:
task_performance = []
target_performance = []

In [110]:
n_epochs = 200

classifier.train()

generator = generator_ls
discriminator = discriminator_ls

opt_G = opt_G_LS
opt_D = opt_D_LS

for epoch in range(0,n_epochs):
    for i, ((imgs_A, labels_A), (imgs_B, labels_B)) in enumerate(zip(dataloader_original,
                                                                 itertools.cycle(usps_data_loader))):
        start = time.time()
        real = Variable(FloatTensor(batch_size, *patch).fill_(1.0), requires_grad=False)
        fake = Variable(FloatTensor(batch_size, *patch).fill_(0.0), requires_grad=False)

        labels_A = Variable(labels_A.type(LongTensor).squeeze())

        imgs_A =  Variable(imgs_A.type(FloatTensor)) 
        imgs_B = Variable(imgs_B.type(FloatTensor)) 
        
        imgs_A_exp = Variable(imgs_A.type(FloatTensor)).expand(batch_size, img_channels, img_size, img_size)

        ####################
        # Train generator
        ####################
        
        opt_G.zero_grad()
         
        # Generate noise: # used to be uniform -1 to 1 # sample from Normal instead?
        z = Variable(FloatTensor(np.random.normal(0,1, (batch_size, latent_dimension)))) 
        
        dataloaded = time.time()
        
        # Generate artificial images based on noise input:
        fake_B = generator(imgs_A, z)
        
        pred_fB = classifier(fake_B, "target")
        task_loss_ = (task_loss(pred_fB, labels_A) + task_loss(classifier(imgs_A,"source"), labels_A)) / 2.
        
        g_loss = lambda_gan * MSE_loss(discriminator(fake_B), real) + lambda_task * task_loss_
        
        g_loss.backward()
        opt_G.step()
        
        gstep = time.time()
        
        ####################
        # Train discriminator
        ####################
        
        opt_D.zero_grad()
        
        real_loss = MSE_loss(discriminator(imgs_B), real)
        fake_loss = MSE_loss(discriminator(fake_B.detach()), fake)
        
        d_loss = (real_loss + fake_loss) / 2
        
        d_loss.backward()
        opt_D.step()
        
        dstep = time.time()
        #############################
        # Evaluate target performance
        #############################
        
        acc = np.mean(np.argmax(pred_fB.data.cpu().numpy(), axis=1) == labels_A.data.cpu().numpy())
        task_performance.append(acc)
        
        pred_B = classifier(imgs_B, "target")
        target_acc = np.mean(np.argmax(pred_B.data.cpu().numpy(), axis=1) == labels_B.numpy())
        target_performance.append(target_acc)
        if len(target_performance) > 100:
            target_performance.pop(0)
        
        
        batches_done = len(dataloader_original) * epoch + i
        
        perf = time.time()
            
        if batches_done%50==0:
            print ("[Epoch %d/%d] [Batch %d/%d] [D loss: %f] [G loss: %f] \
            [domain-translated acc: %3d%% (%3d%%), target-domain acc: %3d%% (%3d%%)]" %
            (epoch, n_epochs,
            i, len(dataloader_original),
            d_loss.data[0], g_loss.data[0],
            100*acc, 100*np.mean(task_performance),
            100*target_acc, 100*np.mean(target_performance)))
            print("Times (total, data, gstep,dstep):",perf-start,dataloaded-start,gstep-dataloaded,dstep-gstep)
        
        interval = 1000
        
        if batches_done % interval == 0:
            sample = torch.cat((imgs_A_exp.data[:5], fake_B.data[:5], imgs_B.data[:5]), -2)
            save_image(sample, 'ls_gan_usps/%d.png' % batches_done, nrow=int(np.sqrt(batch_size)), normalize=True)        
            
        
        

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:86: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number


[Epoch 0/200] [Batch 0/1875] [D loss: 0.514254] [G loss: 2.366608]             [domain-translated acc:   9% (  9%), target-domain acc:   9% (  9%)]
Times (total, data, gstep,dstep): 0.042795658111572266 0.001352071762084961 0.027301311492919922 0.011885643005371094
[Epoch 0/200] [Batch 50/1875] [D loss: 0.378470] [G loss: 1.820933]             [domain-translated acc:  15% ( 10%), target-domain acc:   9% ( 14%)]
Times (total, data, gstep,dstep): 0.028824329376220703 0.00063323974609375 0.014347314834594727 0.012168407440185547
[Epoch 0/200] [Batch 100/1875] [D loss: 0.255474] [G loss: 1.645395]             [domain-translated acc:   9% ( 10%), target-domain acc:  34% ( 20%)]
Times (total, data, gstep,dstep): 0.02845454216003418 0.0008027553558349609 0.016364097595214844 0.010042667388916016
[Epoch 0/200] [Batch 150/1875] [D loss: 0.217816] [G loss: 0.453987]             [domain-translated acc:  81% ( 22%), target-domain acc:  50% ( 32%)]
Times (total, data, gstep,dstep): 0.03171420097351

[Epoch 0/200] [Batch 1550/1875] [D loss: 0.174002] [G loss: 0.142683]             [domain-translated acc:  93% ( 80%), target-domain acc:  84% ( 80%)]
Times (total, data, gstep,dstep): 0.028245210647583008 0.0006186962127685547 0.015421390533447266 0.010704994201660156
[Epoch 0/200] [Batch 1600/1875] [D loss: 0.238099] [G loss: 0.062364]             [domain-translated acc:  96% ( 80%), target-domain acc:  75% ( 82%)]
Times (total, data, gstep,dstep): 0.026958227157592773 0.0006380081176757812 0.014533042907714844 0.010383129119873047
[Epoch 0/200] [Batch 1650/1875] [D loss: 0.277549] [G loss: 0.231141]             [domain-translated acc:  90% ( 80%), target-domain acc:  93% ( 81%)]
Times (total, data, gstep,dstep): 0.0279691219329834 0.0007023811340332031 0.016166210174560547 0.009775400161743164
[Epoch 0/200] [Batch 1700/1875] [D loss: 0.233390] [G loss: 0.359956]             [domain-translated acc:  87% ( 81%), target-domain acc:  84% ( 78%)]
Times (total, data, gstep,dstep): 0.02951

[Epoch 1/200] [Batch 1225/1875] [D loss: 0.069407] [G loss: 0.200801]             [domain-translated acc:  90% ( 86%), target-domain acc:  93% ( 85%)]
Times (total, data, gstep,dstep): 0.029439210891723633 0.0007760524749755859 0.01608586311340332 0.01107025146484375
[Epoch 1/200] [Batch 1275/1875] [D loss: 0.051374] [G loss: 0.184315]             [domain-translated acc:  93% ( 87%), target-domain acc:  87% ( 85%)]
Times (total, data, gstep,dstep): 0.0330657958984375 0.0006928443908691406 0.017398357391357422 0.013420343399047852
[Epoch 1/200] [Batch 1325/1875] [D loss: 0.159159] [G loss: 0.094533]             [domain-translated acc:  96% ( 87%), target-domain acc:  71% ( 84%)]
Times (total, data, gstep,dstep): 0.02987837791442871 0.0007033348083496094 0.0160219669342041 0.011631965637207031
[Epoch 1/200] [Batch 1375/1875] [D loss: 0.087146] [G loss: 0.113105]             [domain-translated acc:  93% ( 87%), target-domain acc:  87% ( 84%)]
Times (total, data, gstep,dstep): 0.0271050930

[Epoch 2/200] [Batch 900/1875] [D loss: 0.114584] [G loss: 0.052661]             [domain-translated acc:  96% ( 89%), target-domain acc:  71% ( 84%)]
Times (total, data, gstep,dstep): 0.029540300369262695 0.0006012916564941406 0.016763925552368164 0.010816812515258789
[Epoch 2/200] [Batch 950/1875] [D loss: 0.042349] [G loss: 0.154369]             [domain-translated acc:  93% ( 89%), target-domain acc:  78% ( 84%)]
Times (total, data, gstep,dstep): 0.03354358673095703 0.0010905265808105469 0.020336389541625977 0.010669231414794922
[Epoch 2/200] [Batch 1000/1875] [D loss: 0.078408] [G loss: 0.251411]             [domain-translated acc:  87% ( 89%), target-domain acc:  90% ( 84%)]
Times (total, data, gstep,dstep): 0.02534651756286621 0.0006477832794189453 0.013992071151733398 0.009385824203491211
[Epoch 2/200] [Batch 1050/1875] [D loss: 0.075340] [G loss: 0.115432]             [domain-translated acc:  93% ( 89%), target-domain acc:  84% ( 84%)]
Times (total, data, gstep,dstep): 0.0284848

...

[Epoch 192/200] [Batch 1600/1875] [D loss: 0.005201] [G loss: 0.041066]             [domain-translated acc: 100% ( 98%), target-domain acc:  68% ( 67%)]
Times (total, data, gstep,dstep): 0.02888035774230957 0.0008225440979003906 0.01626443862915039 0.010364770889282227
[Epoch 192/200] [Batch 1650/1875] [D loss: 0.013355] [G loss: 0.100760]             [domain-translated acc:  96% ( 98%), target-domain acc:  78% ( 69%)]
Times (total, data, gstep,dstep): 0.03156852722167969 0.0008361339569091797 0.0170285701751709 0.012210369110107422
[Epoch 192/200] [Batch 1700/1875] [D loss: 0.060704] [G loss: 0.077911]             [domain-translated acc:  96% ( 98%), target-domain acc:  71% ( 70%)]
Times (total, data, gstep,dstep): 0.027373552322387695 0.0006377696990966797 0.01492452621459961 0.010388612747192383
[Epoch 192/200] [Batch 1750/1875] [D loss: 0.004129] [G loss: 0.048324]             [domain-translated acc: 100% ( 98%), target-domain acc:  75% ( 68%)]
Times (total, data, gstep,dstep): 0.0

[Epoch 193/200] [Batch 1275/1875] [D loss: 0.005911] [G loss: 0.061142]             [domain-translated acc:  96% ( 98%), target-domain acc:  56% ( 67%)]
Times (total, data, gstep,dstep): 0.027085065841674805 0.0005981922149658203 0.01504659652709961 0.009984970092773438
[Epoch 193/200] [Batch 1325/1875] [D loss: 0.011912] [G loss: 0.057391]             [domain-translated acc: 100% ( 98%), target-domain acc:  75% ( 68%)]
Times (total, data, gstep,dstep): 0.026665210723876953 0.0006251335144042969 0.014197587966918945 0.010435819625854492
[Epoch 193/200] [Batch 1375/1875] [D loss: 0.002870] [G loss: 0.052993]             [domain-translated acc: 100% ( 98%), target-domain acc:  65% ( 69%)]
Times (total, data, gstep,dstep): 0.02798748016357422 0.0007026195526123047 0.014833211898803711 0.010983467102050781
[Epoch 193/200] [Batch 1425/1875] [D loss: 0.015261] [G loss: 0.051494]             [domain-translated acc: 100% ( 98%), target-domain acc:  56% ( 67%)]
Times (total, data, gstep,dstep):

[Epoch 194/200] [Batch 950/1875] [D loss: 0.030490] [G loss: 0.047840]             [domain-translated acc: 100% ( 98%), target-domain acc:  68% ( 69%)]
Times (total, data, gstep,dstep): 0.029515981674194336 0.0007417201995849609 0.016028881072998047 0.011246681213378906
[Epoch 194/200] [Batch 1000/1875] [D loss: 0.008640] [G loss: 0.062293]             [domain-translated acc: 100% ( 98%), target-domain acc:  68% ( 71%)]
Times (total, data, gstep,dstep): 0.031057119369506836 0.0006439685821533203 0.01611185073852539 0.012677192687988281
[Epoch 194/200] [Batch 1050/1875] [D loss: 0.000904] [G loss: 0.060887]             [domain-translated acc: 100% ( 98%), target-domain acc:  71% ( 70%)]
Times (total, data, gstep,dstep): 0.02654290199279785 0.0006167888641357422 0.014274120330810547 0.009941816329956055
[Epoch 194/200] [Batch 1100/1875] [D loss: 0.028685] [G loss: 0.043337]             [domain-translated acc: 100% ( 98%), target-domain acc:  65% ( 68%)]
Times (total, data, gstep,dstep): 

Process Process-7859:
Process Process-7857:
Process Process-7858:
Process Process-7856:
Process Process-7860:
Process Process-7855:
Traceback (most recent call last):
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing

KeyboardInterrupt: 

## Save/Load trained models and results

In [28]:
# torch.save(generator,'generator_200k_usps_ls.pt')
# torch.save(discriminator,'discriminator_200k_usps_ls.pt')
# torch.save(classifier,'classifier_g_200k_usps_ls.pt')

# MNIST-M
generator = torch.load('generator_200k.pt')
discriminator = torch.load('discriminator_200k.pt')
classifier = torch.load('classifier_g_200k.pt')

# USPS DA
# generator = torch.load('generator_200k_usps.pt')
# discriminator = torch.load('discriminator_200k_usps.pt')
# classifier = torch.load('classifier_g_200k_usps.pt')

# # USPS LS 
# generator = torch.load('generator_200k_usps_ls.pt')
# discriminator = torch.load('discriminator_200k_usps_ls.pt')
# classifier = torch.load('classifier_g_200k_usps_ls.pt')

## Vizualize latent space

In [117]:
iterate = iter(dataloader_base)

In [244]:
imgs, labels = next(iterate)
num=10
print(labels[0])
single_digit = imgs[0:1,:,:,:].expand(num,-1,-1,-1)
single_label = labels[0]
imgs =  Variable(single_digit.type(FloatTensor)) #.expand(num, 3, img_size, img_size) # expand if MNISTM

z = Variable(FloatTensor(np.ones((num, 10))*np.linspace(0,0.9,num).reshape(num,1))) # linearly interpolate that from 0 to 10?

fake_B = generator(imgs, z)
sample = fake_B 
save_image(sample, 'vars.png', nrow=1, normalize=True)        

tensor(9)


## L2 distance finder

In [247]:
l2_target_img = sample[9,:,:,:].cpu()

In [250]:
diff_list = []
for (imgs, labels) in dataloader_MNISTM_L2: # batch size=1
    diff_list.append(torch.sum((imgs-l2_target_img)**2)) 

In [252]:
save_image(training_set_m.__getitem__(np.argmin(np.array(diff_list)))[0], 'vars_l2.png', nrow=1, normalize=True)  

In [253]:
save_image(l2_target_img, 'vars_l3.png', nrow=1, normalize=True)  

## Train the classifier (evaluation)

In [38]:
simple_classifier =  Classifier_DA().cuda() 
simple_classifier.apply(weights_initialization);

classifier_performance = []

lr_C = 1e-3 
opt_C = torch.optim.Adam(itertools.chain( simple_classifier.parameters()),
                        lr = lr_C, betas = (beta_1, beta_2))

In [39]:
n_epochs = 20
simple_classifier.train()

for epoch in range(n_epochs):
    for i, (imgs, labels) in enumerate(dataloader_MNISTM): # noh
        
        imgs_A =  Variable(imgs.type(FloatTensor))#.expand(batch_size, 3, img_size, img_size) # expand if MNIST
  
        labels_var = Variable(labels.type(LongTensor))
        labels = labels.type(LongTensor)
        
        z = Variable(FloatTensor(np.random.uniform(0,1, (batch_size, latent_dimension)))) # 10 is dataloader batch size
        
        # Generate artificial images based on noise input:
#         augumented_imgs = generator(imgs_A, z)

        opt_C.zero_grad()
        
#         output = simple_classifier(augumented_imgs, "target")
        output = simple_classifier(imgs_A, "target")


        c_loss = task_loss(output, labels_var)
        c_loss.backward()
        opt_C.step()
            
        acc = np.mean(np.array((torch.max(output.data, 1)[1] == labels).cpu()))
        
        classifier_performance.append(acc)
        
        print ("[Epoch %d/%d] [Batch %d/%d] [C loss: %f] \
                [CLF acc: %3d%% (%3d%%)]" %
                (epoch, n_epochs,
                i, len(dataloader_MNISTM),
                c_loss.data[0],
                100*acc, 100*np.mean(classifier_performance[-100:])))
        

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:39: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number


[Epoch 0/20] [Batch 0/1875] [C loss: 2.311460]                 [CLF acc:  12% ( 12%)]
[Epoch 0/20] [Batch 1/1875] [C loss: 2.304763]                 [CLF acc:   9% ( 10%)]
[Epoch 0/20] [Batch 2/1875] [C loss: 2.318113]                 [CLF acc:   9% ( 10%)]
[Epoch 0/20] [Batch 3/1875] [C loss: 2.294397]                 [CLF acc:  15% ( 11%)]
[Epoch 0/20] [Batch 4/1875] [C loss: 2.294818]                 [CLF acc:   6% ( 10%)]
[Epoch 0/20] [Batch 5/1875] [C loss: 2.297511]                 [CLF acc:   6% (  9%)]
[Epoch 0/20] [Batch 6/1875] [C loss: 2.274321]                 [CLF acc:  25% ( 12%)]
[Epoch 0/20] [Batch 7/1875] [C loss: 2.364453]                 [CLF acc:   9% ( 11%)]
[Epoch 0/20] [Batch 8/1875] [C loss: 2.320479]                 [CLF acc:   6% ( 11%)]
[Epoch 0/20] [Batch 9/1875] [C loss: 2.308775]                 [CLF acc:  15% ( 11%)]
[Epoch 0/20] [Batch 10/1875] [C loss: 2.322279]                 [CLF acc:   0% ( 10%)]
[Epoch 0/20] [Batch 11/1875] [C loss: 2.323424]      

[Epoch 0/20] [Batch 112/1875] [C loss: 0.676835]                 [CLF acc:  68% ( 49%)]
[Epoch 0/20] [Batch 113/1875] [C loss: 0.791463]                 [CLF acc:  71% ( 50%)]
[Epoch 0/20] [Batch 114/1875] [C loss: 0.627999]                 [CLF acc:  75% ( 51%)]
[Epoch 0/20] [Batch 115/1875] [C loss: 0.639335]                 [CLF acc:  78% ( 51%)]
[Epoch 0/20] [Batch 116/1875] [C loss: 0.609235]                 [CLF acc:  75% ( 52%)]
[Epoch 0/20] [Batch 117/1875] [C loss: 0.677949]                 [CLF acc:  78% ( 53%)]
[Epoch 0/20] [Batch 118/1875] [C loss: 1.149426]                 [CLF acc:  75% ( 53%)]
[Epoch 0/20] [Batch 119/1875] [C loss: 0.694759]                 [CLF acc:  78% ( 54%)]
[Epoch 0/20] [Batch 120/1875] [C loss: 0.779499]                 [CLF acc:  71% ( 54%)]
[Epoch 0/20] [Batch 121/1875] [C loss: 0.544542]                 [CLF acc:  87% ( 55%)]
[Epoch 0/20] [Batch 122/1875] [C loss: 0.561182]                 [CLF acc:  78% ( 56%)]
[Epoch 0/20] [Batch 123/1875] [C

[Epoch 0/20] [Batch 226/1875] [C loss: 0.261747]                 [CLF acc:  90% ( 83%)]
[Epoch 0/20] [Batch 227/1875] [C loss: 0.263173]                 [CLF acc:  90% ( 83%)]
[Epoch 0/20] [Batch 228/1875] [C loss: 0.476842]                 [CLF acc:  78% ( 83%)]
[Epoch 0/20] [Batch 229/1875] [C loss: 0.387275]                 [CLF acc:  81% ( 83%)]
[Epoch 0/20] [Batch 230/1875] [C loss: 0.212150]                 [CLF acc:  93% ( 83%)]
[Epoch 0/20] [Batch 231/1875] [C loss: 0.300151]                 [CLF acc:  90% ( 83%)]
[Epoch 0/20] [Batch 232/1875] [C loss: 0.170363]                 [CLF acc:  93% ( 83%)]
[Epoch 0/20] [Batch 233/1875] [C loss: 0.331489]                 [CLF acc:  90% ( 83%)]
[Epoch 0/20] [Batch 234/1875] [C loss: 0.269916]                 [CLF acc:  90% ( 83%)]
[Epoch 0/20] [Batch 235/1875] [C loss: 0.174043]                 [CLF acc:  90% ( 84%)]
[Epoch 0/20] [Batch 236/1875] [C loss: 0.290867]                 [CLF acc:  90% ( 84%)]
[Epoch 0/20] [Batch 237/1875] [C

[Epoch 0/20] [Batch 343/1875] [C loss: 0.192891]                 [CLF acc:  87% ( 88%)]
[Epoch 0/20] [Batch 344/1875] [C loss: 0.221882]                 [CLF acc:  93% ( 88%)]
[Epoch 0/20] [Batch 345/1875] [C loss: 0.500202]                 [CLF acc:  87% ( 88%)]
[Epoch 0/20] [Batch 346/1875] [C loss: 0.131288]                 [CLF acc: 100% ( 88%)]
[Epoch 0/20] [Batch 347/1875] [C loss: 0.613289]                 [CLF acc:  78% ( 88%)]
[Epoch 0/20] [Batch 348/1875] [C loss: 0.138533]                 [CLF acc:  93% ( 88%)]
[Epoch 0/20] [Batch 349/1875] [C loss: 0.392440]                 [CLF acc:  96% ( 88%)]
[Epoch 0/20] [Batch 350/1875] [C loss: 0.169197]                 [CLF acc:  96% ( 88%)]
[Epoch 0/20] [Batch 351/1875] [C loss: 0.268732]                 [CLF acc:  90% ( 88%)]
[Epoch 0/20] [Batch 352/1875] [C loss: 0.269612]                 [CLF acc:  93% ( 88%)]
[Epoch 0/20] [Batch 353/1875] [C loss: 0.164486]                 [CLF acc:  90% ( 88%)]
[Epoch 0/20] [Batch 354/1875] [C

...

[Epoch 19/20] [Batch 1377/1875] [C loss: 0.015565]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1378/1875] [C loss: 0.001814]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1379/1875] [C loss: 0.000292]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1380/1875] [C loss: 0.040897]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1381/1875] [C loss: 0.035668]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1382/1875] [C loss: 0.079740]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1383/1875] [C loss: 0.000000]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1384/1875] [C loss: 0.001297]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1385/1875] [C loss: 0.000066]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1386/1875] [C loss: 0.000072]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1387/1875] [C loss: 0.000009]                 [CLF acc: 100% ( 99%)]
[Epoch 19/

[Epoch 19/20] [Batch 1487/1875] [C loss: 0.073886]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1488/1875] [C loss: 0.031848]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1489/1875] [C loss: 0.000000]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1490/1875] [C loss: 0.049975]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1491/1875] [C loss: 0.011762]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1492/1875] [C loss: 0.000001]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1493/1875] [C loss: 0.000002]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1494/1875] [C loss: 0.000130]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1495/1875] [C loss: 0.009541]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1496/1875] [C loss: 0.000216]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1497/1875] [C loss: 0.000078]                 [CLF acc: 100% ( 99%)]
[Epoch 19/

[Epoch 19/20] [Batch 1600/1875] [C loss: 0.000294]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1601/1875] [C loss: 0.000000]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1602/1875] [C loss: 0.000069]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1603/1875] [C loss: 0.018266]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1604/1875] [C loss: 0.000295]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1605/1875] [C loss: 0.000048]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1606/1875] [C loss: 0.000002]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1607/1875] [C loss: 0.000000]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1608/1875] [C loss: 0.090338]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1609/1875] [C loss: 0.007394]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1610/1875] [C loss: 0.015272]                 [CLF acc: 100% ( 99%)]
[Epoch 19/

[Epoch 19/20] [Batch 1717/1875] [C loss: 0.000002]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1718/1875] [C loss: 0.088515]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1719/1875] [C loss: 0.100605]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1720/1875] [C loss: 0.003919]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1721/1875] [C loss: 0.000019]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1722/1875] [C loss: 0.000169]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1723/1875] [C loss: 0.000028]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1724/1875] [C loss: 0.003860]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1725/1875] [C loss: 0.155380]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1726/1875] [C loss: 0.000005]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1727/1875] [C loss: 0.175595]                 [CLF acc:  96% ( 99%)]
[Epoch 19/

[Epoch 19/20] [Batch 1833/1875] [C loss: 0.000065]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1834/1875] [C loss: 0.000000]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1835/1875] [C loss: 0.000169]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1836/1875] [C loss: 0.175425]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1837/1875] [C loss: 0.000224]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1838/1875] [C loss: 0.007111]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1839/1875] [C loss: 0.000027]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1840/1875] [C loss: 0.038459]                 [CLF acc:  96% ( 99%)]
[Epoch 19/20] [Batch 1841/1875] [C loss: 0.000616]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1842/1875] [C loss: 0.001145]                 [CLF acc: 100% ( 99%)]
[Epoch 19/20] [Batch 1843/1875] [C loss: 0.000014]                 [CLF acc: 100% ( 99%)]
[Epoch 19/

In [40]:
classifier_performance_val = []

for i, (imgs, labels) in enumerate(dataloader_MNISTM_test): 
        
    imgs =  Variable(imgs.type(FloatTensor)) #.expand(batch_size, 3, img_size, img_size) # expand if MNISTM
    labels = labels.type(LongTensor)
        
    output = simple_classifier(imgs, "target")

    acc = np.mean(np.array((torch.max(output.data, 1)[1] == labels).cpu()))

    classifier_performance_val.append(acc)

In [41]:
np.mean(classifier_performance_val) 

0.9615615015974441